In [1]:
import os
os.environ['http_proxy'] = 'http://192.41.170.23:3128'
os.environ['https_proxy'] = 'http://192.41.170.23:3128'

In [24]:
import pandas as pd
import sys         
sys.path.append('/home/pranisaa/working_dir/Text-Summarization')        
from config import *

In [20]:
model_params = model_params
data = data
print(model_params)
print(data)

{'MODEL': 't5-small', 'TRAIN_BATCH_SIZE': 16, 'VALID_BATCH_SIZE': 16, 'TRAIN_EPOCHS': 10, 'VAL_EPOCHS': 1, 'LEARNING_RATE': 2e-05, 'SCHEDULER': 'linear', 'MAX_SOURCE_TEXT_LENGTH': 512, 'MAX_TARGET_TEXT_LENGTH': 36, 'SEED': 42}
xsum


In [17]:
from transformers import T5Tokenizer, T5ForConditionalGeneration
from bertviz import model_view
utils.logging.set_verbosity_error()  # Suppress standard warnings

In [85]:
tokenizer = T5Tokenizer.from_pretrained(f"""../model/{model_params["MODEL"]}_{data}/model_files""")
# tokenizer =T5Tokenizer.from_pretrained(model_params["MODEL"])
model = T5ForConditionalGeneration.from_pretrained(f"""../model/{model_params["MODEL"]}_{data}/model_files""", output_attentions=True)
# model = T5ForConditionalGeneration.from_pretrained(model_params["MODEL"], output_attentions=True)

In [86]:
path = '../model/t5-small_xsum/result_eval/predictions_t5-small_epoch0.csv'
df = pd.read_csv(path)
df.head()

Unnamed: 0       ids                                     Generated Text  \
0           0  32240513  Charles Henry Chester, 86, was killed when his...   
1           1  34503579  the benchmark FTSE 100 index was down 44.98 po...   
2           2  22006050  the ex-minister had until now denied a report ...   
3           3  35200357  Steven Gerrard has played 12 games since arriv...   
4           4  35115347  more than 3,000 listed places of worship in Wa...   

                                         Actual Text  BERTScore(precision)  \
0  Northumbria Police has named two people who di...             -0.008147   
1  (Close): London's leading shares dipped in Mon...             -0.220022   
2  Former French Budget Minister Jerome Cahuzac h...             -0.017659   
3  Shrewsbury Town defender Anthony Gerrard hopes...              0.162260   
4  An action plan has been launched to save histo...              0.265505   

   BERTScore(recall)  BERTScore(f1)  RougeScore1  RougeScore2  RougeScoreL  \
0           0.212125       0.101049    12.500000     0.000000     8.333333   
1          -0.025412      -0.122852     8.695652     0.000000     8.695652   
2           0.069007       0.026881    14.705882     0.000000     5.882353   
3           0.200185       0.182483    18.461538     3.174603     9.230769   
4           0.381646       0.324037    25.000000     4.347826    16.666667   

   RougeScoreLsum  
0        8.333333  
1        8.695652  
2        5.882353  
3        9.230769  
4       16.666667

In [87]:
actual = df['Actual Text']
summary = df['Generated Text']

In [88]:
encoder_input_ids = tokenizer([actual[0]], max_length = model_params['MAX_SOURCE_TEXT_LENGTH'], truncation=True, return_tensors="pt").input_ids
decoder_input_ids = tokenizer([summary[0]], max_length = model_params['MAX_TARGET_TEXT_LENGTH'], return_tensors="pt").input_ids

outputs = model(input_ids=encoder_input_ids, decoder_input_ids=decoder_input_ids)

encoder_text = tokenizer.convert_ids_to_tokens(encoder_input_ids[0])
decoder_text = tokenizer.convert_ids_to_tokens(decoder_input_ids[0])

In [89]:
from bertviz import model_view
model_view(
    encoder_attention=outputs.encoder_attentions,
    decoder_attention=outputs.decoder_attentions,
    cross_attention=outputs.cross_attentions,
    encoder_tokens= encoder_text,
    decoder_tokens = decoder_text
)

<IPython.core.display.Javascript object>

In [54]:
model_name = "microsoft/xtremedistil-l12-h384-uncased"  # Find popular HuggingFace models here: https://huggingface.co/models
input_text = "The cat sat on the mat"  
model = AutoModel.from_pretrained(model_name, output_attentions=True)  # Configure model to return attention values
tokenizer = AutoTokenizer.from_pretrained(model_name)
inputs = tokenizer.encode(input_text, return_tensors='pt')  # Tokenize input text
outputs = model(inputs)  # Run model
attention = outputs[-1]  # Retrieve attention from model outputs
tokens = tokenizer.convert_ids_to_tokens(inputs[0])  # Convert input ids to token strings
model_view(attention, tokens)  # Display model view


<IPython.core.display.Javascript object>